### comment out the code below to install required packages

In [1]:
# code to install all the packages we need
# %pip install numpy
# %pip install pandas
# %pip install yfinance
# %pip install requests
# %pip install beautifulsoup4
# %pip install scikit-learn
# %pip install TA-Lib
# %pip install joblib
# %pip install pickle-mixin
# %pip install riskfolio-lib

In [2]:
# Import necessary libraries
import numpy as np
import pandas as pd
import yfinance as yf
from ibapi.client import *
from ibapi.wrapper import *
from ibapi.contract import *
from ibapi.order import *
import ibapi

import requests
import bs4 as bs
import datetime
import time
import threading
from sklearn.pipeline import Pipeline
from sklearn.preprocessing import StandardScaler
from sklearn.svm import SVC
from sklearn.ensemble import RandomForestClassifier
from sklearn.model_selection import GridSearchCV  
from sklearn.model_selection import RandomizedSearchCV

import joblib
import pickle

from scipy.stats import randint, uniform

import talib as ta
from talib import MA_Type


In [3]:
init_event = threading.Event() # init event
id_event = threading.Event()
mkt_event = threading.Event()
hist_event = threading.Event()
order_event = threading.Event()
evec_event = threading.Event()
port_event = threading.Event()
value_event = threading.Event()

In [4]:
# define the App class
class App(EClient, EWrapper):
    def __init__(self, address, port, cid):
        EClient.__init__(self, self)
        # # list to store data
        self.bar_dict = {}
        self.mkt_price = []
        # create a connection with IBKR
        self.connect(address, port, cid)
        self.last_portfolio = pd.DataFrame(columns=["ticker","quantity","marketPrice","marketValue","averageCost","unrealizedPNL","realizedPNL"])
        self.value = 0
        # start client
        thread = threading.Thread(target=self.run)
        thread.start()
        init_event.set()


    def nextValidId(self, orderId: int):
        # provide a new order id for each of my requests
        super().nextValidId(orderId)
        logging.debug("setting nextValidOrderId: %d", orderId)
        self.nextValidOrderId = orderId
        print("NextValidId:", orderId)
        id_event.set()

    def tickPrice(self, reqId: int, tickType: int, price: float, attrib: ibapi.common.TickAttrib):
            print("Tick Price. Ticker Id:", reqId, "tickType:", tickType, "Price:", price)
            if tickType == 9: # if tickType is Close Price
                self.mkt_price.append([reqId, price])
                mkt_event.set()

    def historicalData(self, reqId, bar):
        if reqId not in self.bar_dict.keys():
            self.bar_dict[reqId] = []
        self.bar_dict[reqId].append(vars(bar))
        
    def historicalDataEnd(self, reqId, start, end):
        print(f"end of historicalData")
        hist_event.set()


    # implement code to monitor trade status and receive confirmation of the trade
    def openOrder(self, orderId: OrderId, contract: Contract, order: Order, orderstate: OrderState):
        # openorder callback
        print(f"openOrder. orderId:{orderId}, contract:{contract}, order:{order}")
        order_event.set()

    def orderStatus(self, orderId: OrderId, status: str, filled: float, reamining: float, avgFillPrice: float,
                    permId: int, parenId: int, lastFillPrice: float, clientId: int, whyHeld:str, mktCapPrice: float):
                    # orderstatus callback
        print(f"orderStatus. orderId: {orderId}, status: {status}, filled: {filled}, remaining:{reamining}, avgFillPrice: {avgFillPrice}, permId:{permId}, parentId:{parenId}, lastFillPrice: {lastFillPrice}, clientId: {clientId}, whyHeld: {whyHeld}, mktCapPrice:{mktCapPrice}")

    def execDetails(self, reqId: int, contract: Contract, execution: Execution):
        print(f"execDetails. reqId: {reqId}, contract: {contract}, execution: {execution}")
        evec_event.set()
    # basically a summary

    def commissionReport(self, commissionReport: CommissionReport):
        super().commissionReport(commissionReport)
        print("CommissionReport.", commissionReport)
        
    # called when query portfolio information
    def updatePortfolio(self, contract, position, marketPrice, marketValue, averageCost, unrealizedPNL, realizedPNL, accountName):
        self.last_portfolio = pd.concat([self.last_portfolio,
                                        pd.DataFrame([[contract.symbol, position, marketPrice, marketValue, averageCost, unrealizedPNL, realizedPNL]],
                                                    columns=self.last_portfolio.columns)],
                                        ignore_index=True)
        port_event.set()

    # query total value
    def accountSummary(self, reqId: int, account: str, tag: str, value: str, currency: str):
        self.value = float(value)
        print("Total value of the account: ", self.value)
    
    def accountSummaryEnd(self, reqId: int):
        print('end of account summary')
        value_event.set()

In [5]:
# Connect to the TWS API
app = App('127.0.0.1', 7497, 1000)
init_event.wait() # wait until it's connected
init_event.clear()

ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:hfarm
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:usfarm.nj
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:jfarm
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:usfuture
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:cashfarm
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:eufarmnj
ERROR:ibapi.wrapper:ERROR -1 2104 Market data farm connection is OK:usfarm
ERROR:ibapi.wrapper:ERROR -1 2106 HMDS data farm connection is OK:euhmds
ERROR:ibapi.wrapper:ERROR -1 2106 HMDS data farm connection is OK:ushmds.nj
ERROR:ibapi.wrapper:ERROR -1 2106 HMDS data farm connection is OK:fundfarm
ERROR:ibapi.wrapper:ERROR -1 2106 HMDS data farm connection is OK:ushmds
ERROR:ibapi.wrapper:ERROR -1 2158 Sec-def data farm connection is OK:secdefil


NextValidId: 44


In [6]:
app.reqMarketDataType(1) # in case it doesn't work, change 1 to 3

In [7]:
#get S&P tickers list from wikipedia
resp = requests.get('http://en.wikipedia.org/wiki/List_of_S%26P_500_companies')
soup = bs.BeautifulSoup(resp.text, 'lxml')
table = soup.find('table', {'class': 'wikitable sortable'})

tickers = []

for row in table.findAll('tr')[1:]:
    ticker_name = row.findAll('td')[0].text
    tickers.append(ticker_name)

#clean list
tickers = [s.replace('\n', '') for s in tickers]

#get data from yfin
start = datetime.datetime(2010, 1, 1)
end = datetime.datetime.now().strftime("%Y-%m-%d")
data = yf.download(tickers, start=start, end=end)

print(data)
#TODO: note we might also need to get data from tws.

[*********************100%***********************]  503 of 503 completed

2 Failed downloads:
- BF.B: No data found for this date range, symbol may be delisted
- BRK.B: No timezone found, symbol may be delisted
                            Adj Close                                     \
                                    A        AAL         AAP        AAPL   
Date                                                                       
2010-01-04 00:00:00-05:00   20.301361   4.496878   37.163250    6.505280   
2010-01-05 00:00:00-05:00   20.080830   5.005958   36.942383    6.516528   
2010-01-06 00:00:00-05:00   20.009483   4.798554   37.264503    6.412873   
2010-01-07 00:00:00-05:00   19.983538   4.939965   37.255291    6.401019   
2010-01-08 00:00:00-05:00   19.977055   4.845691   37.402546    6.443573   
...                               ...        ...         ...         ...   
2023-03-02 00:00:00-05:00  141.669998  16.120001  139.210007  145.910004   
2023-03-03 00:00:00-05:00  14

In [8]:
data.to_pickle('SP500_data.pkl')

In [9]:
# data = pd.read_pickle('SP500_data.pkl')

# data cleaning part

In [10]:
#clean data
df = data.stack().reset_index().rename(index=str, columns={"level_1": "Symbol"}).sort_values(['Symbol','Date'])
df.set_index('Date', inplace=True)

#drop tickers not in the list
tickers.remove("BRK.B")
tickers.remove("BF.B")
tickers.remove("FTV")
tickers.remove("GEHC")

#sort by group
groups = df.groupby("Symbol")
Ticker_Data = {}

# check if we have missing values in the last day.
missing_col = []
for t in tickers:
    Ticker_Data[t] = groups.get_group(t)
    if Ticker_Data[t].iloc[-1,:].isnull().any():
        missing_col.append(t)

In [11]:
missing_col

[]

In [12]:
last_X = {} # use the last day's data to make prediction

for t in tickers:
    # AD - Chaikin A/D Line :Volume Indicator
    Ticker_Data[t].loc[:,'AD'] = ta.AD(Ticker_Data[t]['High'], Ticker_Data[t]['Low'], Ticker_Data[t]['Close'], Ticker_Data[t]['Volume'])

    # BBAND
    Ticker_Data[t].loc[:,'Upper BBand'], Ticker_Data[t].loc[:,'Middle BBand'],Ticker_Data[t].loc[:,'Lower BBand']= ta.BBANDS(Ticker_Data[t]['Close'],
                                                                                                       timeperiod=20)
    #NATR - Normalized Average True Range :Volatility Indicator
    Ticker_Data[t].loc[:,'NATR'] = ta.NATR(Ticker_Data[t]['High'], Ticker_Data[t]['Low'], Ticker_Data[t]['Close'], timeperiod=8)
    # MACD
    Ticker_Data[t].loc[:,'Macd'], Ticker_Data[t].loc[:,'Macd Signal'],Ticker_Data[t].loc[:,'Macd Hist'] = ta.MACD(Ticker_Data[t]['Close'], fastperiod=12, slowperiod=26, 
                                                               signalperiod=8)
    # DX Directional Movement Index: momentum indicator
    Ticker_Data[t].loc[:,'DX_8d'] = ta.DX(Ticker_Data[t]['High'], Ticker_Data[t]['Low'], Ticker_Data[t]['Close'], timeperiod=8)
    # momentum
    Ticker_Data[t].loc[:,'Momentum_30d'] = ta.MOM(Ticker_Data[t]['Close'],timeperiod=30)
    Ticker_Data[t].loc[:,'Momentum_15d'] = ta.MOM(Ticker_Data[t]['Close'],timeperiod=15)
    Ticker_Data[t].loc[:,'Momentum_11d'] = ta.MOM(Ticker_Data[t]['Close'],timeperiod=11)
    Ticker_Data[t].loc[:,'Momentum_8d'] = ta.MOM(Ticker_Data[t]['Close'],timeperiod=8)
    Ticker_Data[t].loc[:,'Momentum_4d'] = ta.MOM(Ticker_Data[t]['Close'],timeperiod=4)
    
    #RSI
    Ticker_Data[t].loc[:,'RSI'] = ta.RSI(np.array(Ticker_Data[t]['Close']), timeperiod=8)

    #ROC
    Ticker_Data[t].loc[:,'ROC'] = ta.ROC(np.array(Ticker_Data[t]['Close']), timeperiod=8)

    last_X[t] = Ticker_Data[t].iloc[-1,:].drop(['Symbol'])

    #log Return
    Ticker_Data[t].loc[:,'Returns'] = np.log(Ticker_Data[t]['Close'].shift(-8)/Ticker_Data[t]['Close']) # I want to predict the return of 7 days after today.

    Ticker_Data[t].dropna(inplace =True)

    # get rid of the 30% data in the middle to reduce noise.
    Ticker_Data[t]=Ticker_Data[t].sort_values(by=['Returns'])
    Ticker_Data[t]=pd.concat([Ticker_Data[t].iloc[:int(np.floor(len(Ticker_Data[t]['Returns'])*0.35)),:],
                            Ticker_Data[t].iloc[int(np.floor(len(Ticker_Data[t]['Returns'])*0.85)):,:]])


/tmp/ipykernel_44897/2790017252.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Ticker_Data[t].loc[:,'AD'] = ta.AD(Ticker_Data[t]['High'], Ticker_Data[t]['Low'], Ticker_Data[t]['Close'], Ticker_Data[t]['Volume'])
/tmp/ipykernel_44897/2790017252.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Ticker_Data[t].loc[:,'Upper BBand'], Ticker_Data[t].loc[:,'Middle BBand'],Ticker_Data[t].loc[:,'Lower BBand']= ta.BBANDS(Ticker_Data[t]['Close'],
/tmp/ipykernel_44897/2790017252.py:8: SettingWithCopyWarning: 
A 

# stock selection

In [13]:
X = []
Y = []

for i in tickers:
    X.append(Ticker_Data[i].drop(columns=['Symbol','Returns']))
    Y.append(Ticker_Data[i]['Returns'].apply(lambda x:1 if (x>np.mean(Ticker_Data[i]['Returns']) and (x>0)) else -1)) # 1 or -1
# turn list into dataframe
X = pd.concat(X)
Y = pd.concat(Y)

In [14]:
# SVM pipeline
# only need to excute it once if it takes too long
pipe = Pipeline([
    ('scaler', StandardScaler()),
    ('classifier', RandomForestClassifier())
])

# define the hyperparameter search space
# define the hyperparameter search space
param_dist = {
    'classifier__n_estimators': randint(100, 500),
    'classifier__max_depth': randint(3, 25),
    'classifier__min_samples_split': randint(2, 10),
    'classifier__min_samples_leaf': randint(1, 6),
    'classifier__max_features': ['sqrt', 'log2'],
}
# define the search parameters
n_iter_search = 10  # number of parameter combinations to try
cv = 5  # number of cross-validation folds

# randomsearch
clf = RandomizedSearchCV(pipe, param_dist, n_iter=n_iter_search, cv=cv, scoring='f1', n_jobs=-1, verbose=2)
result = clf.fit(X, Y)

Fitting 5 folds for each of 10 candidates, totalling 50 fits


ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.hfarm
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.jfarm
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.hfarm
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.jfarm
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.usfuture
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.usfuture
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.eufarmnj
ERROR:ibapi.wrapper:ERROR -1 2108 Market data farm connection is inactive but should be available upon demand.eufarmnj


[CV] END classifier__max_depth=18, classifier__max_features=sqrt, classifier__min_samples_leaf=3, classifier__min_samples_split=7, classifier__n_estimators=269; total time=22.6min
[CV] END classifier__max_depth=18, classifier__max_features=sqrt, classifier__min_samples_leaf=3, classifier__min_samples_split=7, classifier__n_estimators=269; total time=22.6min
[CV] END classifier__max_depth=18, classifier__max_features=sqrt, classifier__min_samples_leaf=3, classifier__min_samples_split=7, classifier__n_estimators=269; total time=22.7min
[CV] END classifier__max_depth=9, classifier__max_features=sqrt, classifier__min_samples_leaf=4, classifier__min_samples_split=7, classifier__n_estimators=434; total time=22.9min
[CV] END classifier__max_depth=9, classifier__max_features=sqrt, classifier__min_samples_leaf=4, classifier__min_samples_split=7, classifier__n_estimators=434; total time=23.1min
[CV] END classifier__max_depth=9, classifier__max_features=sqrt, classifier__min_samples_leaf=4, class

RandomizedSearchCV(cv=5,
                   estimator=Pipeline(steps=[('scaler', StandardScaler()),
                                             ('classifier',
                                              RandomForestClassifier())]),
                   n_jobs=-1,
                   param_distributions={'classifier__max_depth': <scipy.stats._distn_infrastructure.rv_discrete_frozen object at 0x7f1cca42d2d0>,
                                        'classifier__max_features': ['sqrt',
                                                                     'log2'],
                                        'classifier__min_samples_leaf': <scipy.stats._distn_infrastructure.rv_discrete_frozen object at 0x7f1cca447640>,
                                        'classifier__min_samples_split': <scipy.stats._distn_infrastructure.rv_discrete_frozen object at 0x7f1cca5c5570>,
                                        'classifier__n_estimators': <scipy.stats._distn_infrastructure.rv_discrete_frozen object at 0x7f1cca5c4fd0>},
                   scoring='f1', verbose=2)

In [ ]:
print(clf.cv_results_)
print('--------------------')
print(clf.scorer_)
print('--------------------')
print(clf.best_score_)
print('--------------------')
print(clf.best_params_)

In [16]:
# retrain the pipeline with the best parameters on the entire dataset
best_pipe = pipe.set_params(**clf.best_params_)
# fit it to the entire data.
best_pipe.fit(X, Y)

# save the resulting model to disk
joblib.dump(best_pipe, 'rf_model_2.joblib')

['rf_model_v2.joblib']

In [14]:
clf = joblib.load('rf_model_2.joblib')
# retrain the model with updated data

# select top ten stocks

In [15]:
probs = []
for t in tickers:
    tmp_X = last_X[t].reset_index(drop=True).to_numpy().reshape(1, -1)
    last_X_df = pd.DataFrame(tmp_X, columns=last_X[t].index)
    probs.append(clf.predict_proba(last_X_df)[:,1][0]) #  how close it is to 1

# sort probabilities in descending order
sorted_probs = np.sort(probs)[::-1]

# set threshold for top ten closest to 1
threshold = sorted_probs[9]

# set top ten closest to 1 to 1, and the rest to 0
tmp_index = np.zeros(len(probs))
tmp_index[probs >= threshold] = 1
tmp_index = tmp_index.astype(int)


In [16]:
portfolio_list = [tickers[i] for i in range(len(tmp_index)) if tmp_index[i] == 1]
portfolio_list

['A', 'AWK', 'AZO', 'BXP', 'IFF', 'MRO', 'MHK', 'MOH', 'PKI', 'VFC']

In [17]:
with open('portfolio_list.pickle', 'wb') as f:
    pickle.dump(portfolio_list, f)

# experiment

In [18]:
# import yfinance as yf

# # Get stock information for Apple
# apple = yf.Ticker("AAPL")

# ## Get the latest financial statement data
# financials = apple.financials 
# # Get the net income
# net_income = financials.loc['Net Income']

# # Get the latest balance sheet data
# balance_sheet = apple.balance_sheet
# # Get the total assets
# total_assets = balance_sheet.loc['Total Assets']
# total_equity = balance_sheet.loc['Total Equity Gross Minority Interest']
# #-------------------------------
# roa = net_income / total_assets
# roe = net_income / total_equity


In [19]:
app.disconnect()